In [1]:
import requests 
from bs4 import BeautifulSoup
import pandas as pd
import spacy
from spacy import displacy

In [2]:
url = "https://www.mckinsey.com/id/our-insights/indonesias-green-powerhouse-promise-ten-big-bets-that-could-pay-off"
response = requests.get(url)

In [3]:
soup=BeautifulSoup(response.content, "html.parser")

In [4]:
print(soup.prettify())

<!DOCTYPE html>
<html dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <meta content="width=device-width, initial-scale=1.0" name="viewport"/>
  <meta content="IE=edge" http-equiv="X-UA-Compatible"/>
  <script>
   var McKinsey = {"ArticleTemplate":"Legacy","DaysSinceCMSPublication":"150","DisplayDate":"4/22/2024","OriginalPublicationDate":"12/18/2023","SitecoreId":"{2BAB2DF4-C270-4063-B4B3-2FC9864EE329}","Title":"Indonesia’s green powerhouse promise: Ten bold moves","ArticleType":"Article","ContentType":"Article","ServerNumber":"","IsPageRestricted":"true","UserID":"","RegistrationDate":"","LoginStatus":"logged_out","JobTitle":"","CompanyName":"","blogTags":null}; var pageMetaInformation = {"CurrentLanguage":"en","AlternateLanguages":[{"DisplayName":"English","LanguageCode":"en","Url":"/id/our-insights/indonesias-green-powerhouse-promise-ten-big-bets-that-could-pay-off"}],"NavigationLink":"indonesia","ActiveItemId":"{B40FC5DD-C81F-49F4-8936-9F93723D8B6A}","OfficeCode":"id","Min

In [5]:
main_content = soup.find('main')
for element in main_content(['aside', 'a', 'span']):
    element.decompose()

In [6]:
text_list = []
stop_text = "By utilizing its abundant resources relevant for the green transition and building on various strategic initiatives across industries and the public and private sectors, the country could position itself well in the global journey to net zero."
for paragraph in main_content.find_all('p'):
    paragraph_text = paragraph.get_text(separator=' ', strip=False)

    if stop_text in paragraph_text:
        text_list.append(paragraph_text)
        break
    text_list.append(paragraph_text)

In [7]:
df = pd.DataFrame(text_list, columns=["Paragraph Text"])
df.to_csv('07_paragraphs.csv', index=False)

In [8]:
df

Paragraph Text
0   The world stands at a pivotal point  in the jo...
1   Challenges include fostering global cooperatio...
2   On the other hand, the transition to sustainab...
3   Global efforts are already underway. These inc...
4   As the eighth-largest contributor to global gr...
5   The country has prioritized green growth, and ...
6   Notably, the Just Energy Transition Partnershi...
7   Finally, Indonesia’s endowment of critical min...
8   In this article, we offer ten strategic initia...
9   Indonesia’s energy sector, including end use e...
10  The Indonesian government aims for net-zero em...
11  The Indonesian government has laid out targets...
12  Fossil fuels currently account for around 95 p...
13  The government has implemented specific local ...
14  To effectively scale up its renewable energy s...
15  In addition, the national grid will need to be...
16  The global transmission market, poised to reac...
17  To expand and modernize its grid, Indonesia ha...
18  Indonesia is also encouraging associated priva...
19  In addition, the government has initiated prog...
20  For Indonesia to accelerate strengthening and ...
21  The transportation sector in Indonesia current...
22  Despite EVs currently holding less than 1 perc...
23  In a net-zero scenario, total EV sales penetra...
24  Total EV penetration is forecast to reach 6 pe...
25  For Indonesia to realize the full potential of...
26  The role of batteries, especially lithium-ion ...
27  Indonesia’s nickel resources and an enabling e...
28  For Indonesia to realize its potential as a gl...
29  High-quality carbon credits (or carbon offsets...
30  Nature-based solutions (NBS) for carbon seques...
31  However, ensuring the long-term viability of t...
32  Momentum for NBS in Indonesia is accelerating,...
33  Ways that Indonesia could position itself as a...
34  Low-carbon transportation cannot be delivered ...
35  Indonesia has taken several steps to increase ...
36  Bioethanol:  E5 bioethanol-blended gasoline wa...
37  Biodiesel:  The biodiesel blend mandate was in...
38  Sustainable aviation fuel (SAF):  With around ...
39  SAF from used cooking oil:  Used cooking oil (...
40  To successfully expand the use of green fuels,...
41  The global importance of CCS as a tool to miti...
42  Indonesia has been actively pursuing CCS, with...
43  To inform effective CCUS implementation, Indon...
44  Indonesia is aiming for between 17 and 19 perc...
45  The Indonesian government has already initiate...
46  The Kalimantan Industrial Park Indonesia (KIPI...
47  To successfully establish and scale green indu...
48  Indonesia has set an ambitious target to reduc...
49  Sustainable financing can take three main form...
50  In Asia, green bonds and sustainability-linked...
51  Blended finance brings a more unique value pro...
52  In Indonesia, significant strides have been ma...
53  Indonesia has seen progress across key financi...
54  These challenges may also erode investor confi...
55  To become a green economy, the integration of ...
56  Indonesia has taken initial steps to lay the f...
57  To enhance its green economic landscape, Indon...
58  Decarbonizing is considerably challenging for ...

In [9]:
nlp = spacy.load("en_core_web_sm")

In [10]:
pip install spacy

Note: you may need to restart the kernel to use updated packages.


In [11]:
pip install https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-3.6.0/en_core_web_sm-3.6.0.tar.gz

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 6.1 MB/s eta 0:00:0000:0100:01
  Preparing metadata (setup.py) ... done
Note: you may need to restart the kernel to use updated packages.


In [12]:
relationship_keywords = {'collaboration', 'cooperation', 'partner', 'engage', 
                         'support', 'fund', 'finance', 'invest', 'develop', 
                         'supply', 'promote', 'transition', 'export', 'agreement', 
                         'interest', 'share', 'enhance', 'effort', 'import'}

In [13]:
def extract_entities_and_relationships(text):
    doc = nlp(text)  # Process text with spaCy
    entities = [(ent.text, ent.label_) for ent in doc.ents if ent.label_ in ['ORG', 'GPE', 'FAC']]

    # Find relationships based on keywords
    relationships = []
    for token in doc:
        if token.lemma_ in relationship_keywords:  # Use lemma_ to check relationship keywords
            subject = [w for w in token.children if w.dep_ == "nsubj"]  # Find subject
            object_ = [w for w in token.children if w.dep_ == "dobj"]  # Find object
            if subject and object_:
                relationships.append((subject[0].text, token.text, object_[0].text))  # (subject, relationship, object)

    return entities, relationships

In [14]:
df['Entities'], df['Relationships'] = zip(*df['Paragraph Text'].apply(extract_entities_and_relationships))

In [15]:
df[['Paragraph Text', 'Entities', 'Relationships']]

Paragraph Text  \
0   The world stands at a pivotal point  in the jo...   
1   Challenges include fostering global cooperatio...   
2   On the other hand, the transition to sustainab...   
3   Global efforts are already underway. These inc...   
4   As the eighth-largest contributor to global gr...   
5   The country has prioritized green growth, and ...   
6   Notably, the Just Energy Transition Partnershi...   
7   Finally, Indonesia’s endowment of critical min...   
8   In this article, we offer ten strategic initia...   
9   Indonesia’s energy sector, including end use e...   
10  The Indonesian government aims for net-zero em...   
11  The Indonesian government has laid out targets...   
12  Fossil fuels currently account for around 95 p...   
13  The government has implemented specific local ...   
14  To effectively scale up its renewable energy s...   
15  In addition, the national grid will need to be...   
16  The global transmission market, poised to reac...   
17  To expand and modernize its grid, Indonesia ha...   
18  Indonesia is also encouraging associated priva...   
19  In addition, the government has initiated prog...   
20  For Indonesia to accelerate strengthening and ...   
21  The transportation sector in Indonesia current...   
22  Despite EVs currently holding less than 1 perc...   
23  In a net-zero scenario, total EV sales penetra...   
24  Total EV penetration is forecast to reach 6 pe...   
25  For Indonesia to realize the full potential of...   
26  The role of batteries, especially lithium-ion ...   
27  Indonesia’s nickel resources and an enabling e...   
28  For Indonesia to realize its potential as a gl...   
29  High-quality carbon credits (or carbon offsets...   
30  Nature-based solutions (NBS) for carbon seques...   
31  However, ensuring the long-term viability of t...   
32  Momentum for NBS in Indonesia is accelerating,...   
33  Ways that Indonesia could position itself as a...   
34  Low-carbon transportation cannot be delivered ...   
35  Indonesia has taken several steps to increase ...   
36  Bioethanol:  E5 bioethanol-blended gasoline wa...   
37  Biodiesel:  The biodiesel blend mandate was in...   
38  Sustainable aviation fuel (SAF):  With around ...   
39  SAF from used cooking oil:  Used cooking oil (...   
40  To successfully expand the use of green fuels,...   
41  The global importance of CCS as a tool to miti...   
42  Indonesia has been actively pursuing CCS, with...   
43  To inform effective CCUS implementation, Indon...   
44  Indonesia is aiming for between 17 and 19 perc...   
45  The Indonesian government has already initiate...   
46  The Kalimantan Industrial Park Indonesia (KIPI...   
47  To successfully establish and scale green indu...   
48  Indonesia has set an ambitious target to reduc...   
49  Sustainable financing can take three main form...   
50  In Asia, green bonds and sustainability-linked...   
51  Blended finance brings a more unique value pro...   
52  In Indonesia, significant strides have been ma...   
53  Indonesia has seen progress across key financi...   
54  These challenges may also erode investor confi...   
55  To become a green economy, the integration of ...   
56  Indonesia has taken initial steps to lay the f...   
57  To enhance its green economic landscape, Indon...   
58  Decarbonizing is considerably challenging for ...   

                                             Entities  \
0                                                  []   
1                                                  []   
2                                                  []   
3   [(China, GPE), (PV, FAC), (GW, ORG), (Norway, ...   
4    [(GHG, ORG), (Indonesia, GPE), (Indonesia, GPE)]   
5   [(Indonesia, GPE), (Indonesia, GPE), (National...   
6   [(the Just Energy Transition Partnership, ORG)...   
7   [(Indonesia, GPE), (EV, ORG), (NBS, ORG), (EV,...   
8    [(Indonesia, GPE), (CCS, GPE), (Indonesia, GPE)]   
9                                  [(Indonesia, 

In [16]:
for index, row in df.iterrows():
    print(f"\nParagraph {index + 1}:")
    print(row['Paragraph Text'])

    # Display dependency parsing
    doc = nlp(row['Paragraph Text'])
    sentence_spans = list(doc.sents)
    displacy.render(sentence_spans, style='dep', jupyter=True, options={'compact': True})
    
    # Display named entities
    displacy.render(sentence_spans, style="ent", jupyter=True)
    
    # Print extracted entities and relationships
    print("Entities:", row['Entities'])
    print("Relationships:", row['Relationships'])


Paragraph 1:
The world stands at a pivotal point  in the journey toward decarbonization—emissions need to reduce by half by 2030 and reduce steeply thereafter.  This presents both immense challenges and significant opportunities.


/Users/loogyee/anaconda3/lib/python3.11/site-packages/spacy/displacy/__init__.py:213: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)


Entities: []
Relationships: []

Paragraph 2:
Challenges include fostering global cooperation; strengthening climate policies; navigating technological transitions (including negative emissions technologies); overcoming infrastructure limitations; and securing substantial investments. In addition, a just transition is needed, one that includes reskilling workers and addressing socioeconomic disparities.


Entities: []
Relationships: []

Paragraph 3:
On the other hand, the transition to sustainability and clean energy presents a tremendous market opportunity, requiring unprecedented global investments of $8 trillion to $11 trillion annually to 2050 (Exhibit 1).  Power generation, transportation, as well as land use, land-use change, and forestry (LULUCF) are three sectors at the forefront of this required transformation.


Entities: []
Relationships: []

Paragraph 4:
Global efforts are already underway. These include China having scaled up solar photovoltaic (PV) capacity to approximately 500 gigawatts (GW), Norway having successfully shifted to more than 80 percent of new car sales being electric vehicles (EVs), and Canada having the world’s largest carbon capture and storage (CCS) facility at 14.6 million metric tons per year (Mtpa).  Developments such as these not only address urgent decarbonization needs, but also open new avenues for economic growth and innovation.


...

Entities: [('Indonesia', 'GPE'), ('Indonesia', 'GPE')]
Relationships: []

Paragraph 56:
To become a green economy, the integration of policy, technology, and people (as well as finance) will be key to unlocking all sectors, with one crucial cross-cutting policy that could have a strong enabling effect on the carbon price (for example, via an Emissions Trading Scheme).  Regarding technology, while many low-carbon technologies are manufactured outside the country, Indonesia could leverage global trends to attract new foreign investment and expertise in low-carbon manufacturing. Indonesia has a demographic advantage with its young, educated, and growing population, which enhances its attractiveness as an investment destination. Opportunities to further entice foreign companies and skilled professionals include financial incentives, robust infrastructure, and favorable visa and tax policies—potentially positioning Indonesia as an appealing alternative to traditional expatriate hubs such as

Entities: [('Indonesia', 'GPE'), ('Indonesia', 'GPE'), ('Indonesia', 'GPE'), ('Dubai', 'GPE'), ('Singapore', 'GPE')]
Relationships: [('which', 'enhances', 'attractiveness')]

Paragraph 57:
Indonesia has taken initial steps to lay the foundation for a green economy. Key initiatives include:


Entities: [('Indonesia', 'GPE')]
Relationships: []

Paragraph 58:
To enhance its green economic landscape, Indonesia could consider the following priority actions:


Entities: [('Indonesia', 'GPE')]
Relationships: []

Paragraph 59:
Decarbonizing is considerably challenging for Indonesia, but the opportunities are equally significant. By utilizing its abundant resources relevant for the green transition and building on various strategic initiatives across industries and the public and private sectors, the country could position itself well in the global journey to net zero.


Entities: [('Indonesia', 'GPE')]
Relationships: []


In [17]:
entity1_list = []
relationship_list = []
entity2_list = []
date_list = []
money_list = []

In [18]:
# Iterate through each paragraph
for index, row in df.iterrows():
    doc = nlp(row['Paragraph Text'])  # Process the paragraph with spaCy

    for sent in doc.sents:
        # Extract named entities (countries, organizations)
        entities = []
        money_in_sentence = []

        for ent in sent.ents:
            if 'Inititative' in ent.text.lower(): 
                ent = ent._replace(label_='POL')
                entities.append(ent)
            elif ent.label_ in ['GPE', 'ORG', 'POL', 'MONEY']:
                entities.append(ent)

            # Collect monetary amounts
            if ent.label_ == "MONEY":
                money_in_sentence.append(ent.text)
        
        # Look for verbs or specific relationship nouns in the sentence
        verbs = [token for token in sent if token.pos_ == "VERB"]
        keywords_in_sentence = [token.text for token in sent if token.lemma_ in relationship_keywords]
        
        # Extract dates
        dates = [ent.text for ent in sent.ents if ent.label_ == "DATE"]

        # If we find two entities and a relationship keyword, we assume a relationship
        if len(entities) >= 2 and keywords_in_sentence:
            entity1_list.append(entities[0].text)

            # Concatenate the relationship noun and verb (if available) into one string
            relationship_info = keywords_in_sentence[0]
            if verbs:
                relationship_info += " (verb: " + verbs[0].lemma_ + ")"

            relationship_list.append(relationship_info)  # Store concatenated info
            entity2_list.append(entities[1].text)
            date_list.append(dates[0] if dates else "n/a")
            money_list.append(money_in_sentence[0] if money_in_sentence else "n/a")

In [19]:
# DataFrame
relationships_df = pd.DataFrame({
    "Entity1": entity1_list,
    "Relationship": relationship_list,
    "Entity2": entity2_list,
    "Date": date_list,
    "Money": money_list
})

In [20]:
relationships_df

Entity1                    Relationship  \
0                           $8 trillion to      transition (verb: present)   
1                                Indonesia        support (verb: increase)   
2   the Just Energy Transition Partnership    transition (verb: establish)   
3                                     JETP               share (verb: aim)   
4                                Indonesia             supply (verb: base)   
5                                Singapore            exports (verb: spur)   
6                                Indonesia            efforts (verb: plan)   
7                               26,000 EVs  transition (verb: participate)   
8                               26,000 EVs  transition (verb: participate)   
9                                  Efforts             Efforts (verb: map)   
10                               Indonesia             support (verb: set)   

                                         Entity2            Date  \
0                                   $11 trillion        annually   
1             Nationally Determined Contribution  September 2022   
2                                      Indonesia            2022   
3                                      Indonesia            2030   
4                                             EV             n/a   
5                                             PV             n/a   
6                              LS Cable & System             n/a   
7                                      Indonesia            2030   
8                                      Indonesia            2030   
9   the Ministry of Energy and Mineral Resources             n/a   
10                                           GHG            2030   

             Money  
0   $8 trillion to  
1              n/a  
2              n/a  
3              n/a  
4              n/a  
5              n/a  
6              n/a  
7       26,000 EVs  
8       26,000 EVs  
9              n/a  
10             n/a

In [21]:
# Export to csv
relationships_df.to_csv('07_relationships.csv', index=False)